In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import statsmodels.api as sm
import numpy as np
import pandas as pd
from sklearn.linear_model import Ridge
from sklearn.linear_model import ElasticNet
import matplotlib.dates as mdates
import plotly.graph_objects as go
import requests

In [ ]:
pd.set_option('display.float_format', lambda x: f'{x:,.4f}')
plt.rcParams['figure.dpi']=1200

In [ ]:
commodities = pd.read_csv('commodities.csv',index_col=0,parse_dates=['time'])
ceer_fx = pd.read_csv('ceer.csv',index_col=0,parse_dates=['time'])
ceernorm = pd.read_csv('CEERNORM.csv',index_col=0,parse_dates=['time'])
al = pd.read_csv('ALUMINIUM.csv',index_col=0,parse_dates=['time'])
ppi = pd.read_csv('PPI.csv')
rmpi = pd.read_csv('RMPI.csv')
trade_data = pd.read_csv('Trade.csv')
detai_trade = pd.read_csv('Det.csv')
cpi = pd.read_csv('cpi.csv',index_col=0,parse_dates=['time'])

In [ ]:
detai_trade.ffill(inplace=True)


In [ ]:
date_cols = [c for c in detai_trade.columns if c not in ["Trade", "Product"]]


imp_total = detai_trade.query("Trade == 'Import' and Product == 'Total of all merchandise'")[date_cols].iloc[0]
imp_energy = detai_trade.query("Trade == 'Import' and Product == 'Energy products'")[date_cols].iloc[0]

exp_total = detai_trade.query("Trade == 'Export' and Product == 'Total of all merchandise'")[date_cols].iloc[0]
exp_energy = detai_trade.query("Trade == 'Export' and Product == 'Energy products'")[date_cols].iloc[0]

imports_non_energy = imp_total - imp_energy
exports_non_energy = exp_total - exp_energy


net_non_energy_balance = exports_non_energy - imports_non_energy
net_non_energy_balance.name = "Net non-energy trade balance"

net_energy_balance = exp_energy - imp_energy
net_energy_balance.name = "Net energy trade balance" 


net_non_energy_df = net_non_energy_balance.to_frame()
net_non_energy_df.index = pd.to_datetime(net_non_energy_df.index, format='%y-%b', errors='coerce')

net_energy_balance_df = net_energy_balance.to_frame()
net_energy_balance_df.index = pd.to_datetime(net_energy_balance.index, format='%y-%b', errors='coerce')

In [ ]:
trade_data.ffill(inplace=True)

imports = trade_data[trade_data['Trade'] == "Import"].drop(["Trade"],axis=1).set_index('Principal trading partners').T
exports = trade_data[trade_data['Trade'] == "Export"].drop(["Trade"],axis=1).set_index('Principal trading partners').T
exports.index = pd.to_datetime(exports.index, format='%y-%b', errors='coerce')
imports.index = pd.to_datetime(imports.index, format='%y-%b', errors='coerce')


In [ ]:
ppi = ppi.set_index('time')


ppi = ppi.T


ppi.index.name = 'time'


ppi.index = pd.to_datetime(ppi.index, format='%y-%b', errors='coerce')


In [ ]:
rmpi = rmpi.set_index('time')


rmpi = rmpi.T


rmpi.index.name = 'time'


rmpi.index = pd.to_datetime(rmpi.index, format='%y-%b', errors='coerce')

In [ ]:
commodities.drop("cotton",axis=1,inplace=True)

In [ ]:
base = "CAD"
usdbase = f"USD_{base}"
assert usdbase in ceer_fx.columns, "USD_CAD column is required."

fx_cols = [c for c in ceer_fx.columns if c.startswith("USD_") and c != usdbase]

cross = pd.DataFrame(index=ceer_fx.index)
for col in fx_cols:
    ccy = col.split("_", 1)[1]                 
    cross[f"{ccy}{base}"] = ceer_fx[usdbase] / ceer_fx[col]  
cross["USDCAD"] = ceer_fx["USD_CAD"]

In [ ]:
commodities = commodities.mul(cross['USDCAD'].reindex(commodities.index), axis=0)

In [ ]:
commodities.dropna(inplace=True)
commodities

ar_coffe   brent     corn     diesel  feeder_cattle     ho  \
time                                                                     
2009-01-02    1.3420 56.7658 498.8637   517.6808       115.6856 1.7913   
2009-01-05    1.2838 59.1470 490.2100   570.7296       115.6240 1.8789   
2009-01-06    1.3725 59.7366 505.3905   608.2419       113.6449 1.9226   
2009-01-07    1.3533 54.3441 493.5525   593.0925       111.9825 1.8286   
2009-01-08    1.3489 53.1126 483.6258   568.6987       111.1715 1.8068   
...              ...     ...      ...        ...            ...    ...   
2025-10-27    5.2291 91.0403 613.6108 1,003.1616       467.5450 3.3732   
2025-10-28    5.1919 88.9278 614.6914   972.1057       452.1581 3.2918   
2025-10-29    5.2252 89.2570 615.9462   981.6794       464.1235 3.3179   
2025-10-30    5.2671 89.5184 613.8797   986.1505       466.8170 3.3402   
2025-10-31    5.2737 90.5032 616.2299   990.5070       463.8711 3.3572   

            lean_hogs  Live_cattle     NG     oats     rb    Soybean  \
time                                                                   
2009-01-02    77.2649     105.3997 7.2255 256.5412 1.3438 1,173.7970   
2009-01-05    74.7146     104.3596 7.2378 257.4720 1.4094 1,172.6896   
2009-01-06    75.6017     104.6838 7.0731 269.5416 1.4059 1,199.1055   
2009-01-07    75.3067     101.6493 6.9583 263.0700 1.2755 1,173.1500   
2009-01-08    74.2293      98.8654 6.6382 265.1470 1.2939 1,175.9210   
...               ...          ...    ...      ...    ...        ...   
2025-10-27   115.4028     317.2107 5.5605 431.6618 2.6200 1,514.9588   
2025-10-28   113.5308     313.4989 5.3494 425.1761 2.6146 1,522.6173   
2025-10-29   113.1863     318.8444 5.3234 422.4583 2.6208 1,518.0881   
2025-10-30   114.0791     321.9076 5.7283 416.8593 2.6278 1,546.9685   
2025-10-31   114.7839     320.3667 5.8273 428.0475 2.6546 1,561.5546   

            Soybean_meal    sugar  us_cotton     wti    wheat  
time                                                           
2009-01-02      364.2401 398.3649     0.5919 56.0760 739.3711  
2009-01-05      356.0504 390.7376     0.5759 58.1815 735.1660  
2009-01-06      355.0147 396.5099     0.5944 57.4313 760.7457  
2009-01-07      349.5750 395.7900     0.5879 50.5166 726.7013  
2009-01-08      355.5110 400.5741     0.5995 49.5813 728.2625  
...                  ...      ...        ...     ...      ...  
2025-10-27      419.1922 583.8714     0.9209 85.5892 750.6918  
2025-10-28      429.9286 575.1800     0.9235 83.7962 754.7025  
2025-10-29      431.9473 573.9198     0.9325 83.5428 755.7931  
2025-10-30      443.0476 572.0036     0.9273 84.1171 749.0157  
2025-10-31      452.1728 575.8110     0.9315 85.0799 761.1633  

[4155 rows x 17 columns]

In [ ]:
merged = pd.merge(commodities,cross,left_index=True,right_index=True)


In [ ]:
monthly = merged.resample('MS').first()
monthly = pd.merge(monthly,al,left_index=True,right_index=True,how='left')
monthly.ffill(inplace=True)

In [ ]:
ppi = pd.merge(monthly,ppi,left_index=True,right_index=True)

In [ ]:
target_col = "IPPI"


ppi_ret = ppi.pct_change(12).dropna()
# ppi_ret = pd.merge(ppi_ret,tbills,right_index=True,left_index=True)
# ppi_ret['1Month'] = ppi_ret['1Month']/100
assets = [c for c in ppi_ret.columns if c != target_col]
R_ippi = ppi_ret[assets]
Y_ippi = ppi_ret[target_col]

In [ ]:
def ridge_with_budget(X, y, alpha=1e-4):
    """
    Solve:  min ||y - Xw||^2 + alpha||w||^2   s.t.  1'w = 1

    X : (T x k) matrix of asset returns
    y : (T,) vector of target (IPPI 12m change)
    alpha : ridge penalty (L2)

    Returns
    -------
    w : (k,) numpy array of portfolio weights
    """
    X = np.asarray(X, float)
    y = np.asarray(y, float)

    T, k = X.shape

    A = X.T @ X + alpha * np.eye(k)
    b = X.T @ y
    ones = np.ones((1, k))


    KKT = np.block([
        [A,      ones.T],
        [ones,   np.zeros((1, 1))]
    ])
    rhs = np.concatenate([b, np.array([1.0])])

    sol = np.linalg.solve(KKT, rhs)
    w = sol[:k]
    return w

In [ ]:
def evaluate_hedge(Y, Y_hat):
    Y, Y_hat = Y.align(Y_hat, join="inner")
    err = Y_hat - Y

    tracking_error_std = err.std()
    corr = np.corrcoef(Y, Y_hat)[0, 1]
    r2 = 1 - ((err**2).sum() / ((Y - Y.mean())**2).sum())
    mean_bias = err.mean()

    return {
        "tracking_error_std": tracking_error_std,
        "R2": r2,
        "corr": corr,
        "mean_bias": mean_bias,
        "window": len(Y)
    }



In [ ]:
rmpi = pd.merge(monthly,rmpi,left_index=True,right_index=True)


In [ ]:
target_col = "RMPI"


rmpi_ret = rmpi.pct_change(12).dropna()
# ppi_ret = pd.merge(ppi_ret,tbills,right_index=True,left_index=True)
# ppi_ret['1Month'] = ppi_ret['1Month']/100
assets = [c for c in rmpi_ret.columns if c != target_col]
R_rmpi = rmpi_ret[assets]
Y_rmpi = rmpi_ret[target_col]

In [ ]:
def dynamic_inflation_hedge_enet(
    R, 
    Y, 
    window=60, 
    alpha=1e-3, 
    l1_ratio=1, 
    base_asset="1Month"
):
    """
    Dynamic Elastic Net hedge with sum(weights) = 1 and shorting allowed.

    At month t:
      - Use data [t-window : t) only (past window) to fit Elastic Net
      - Enforce sum(weights)=1 via base-asset reparametrization
      - Use those weights with R_t to predict Y_t

    Parameters
    ----------
    R : pd.DataFrame
        Asset returns, index = dates, columns = asset names (incl. base_asset).
    Y : pd.Series
        Target series (e.g., IPPI 12m change or RMPI 12m change).
    window : int
        Rolling window length in months.
    alpha : float
        Overall regularization strength for Elastic Net.
    l1_ratio : float
        0 = pure ridge, 1 = pure lasso. Something like 0.2–0.5 is typical.
    base_asset : str
        Column in R used as the "anchor" to enforce sum(weights) = 1.

    Returns
    -------
    weights : pd.DataFrame
        Portfolio weights over time. Each row sums to ~1.
    Y_hat : pd.Series
        One-step-ahead predictions for Y.
    """

    # Align
    R, Y = R.align(Y, join="inner", axis=0)
    R = R[~R.index.duplicated(keep="last")]
    Y = Y[~Y.index.duplicated(keep="last")]

    assets = list(R.columns)
    if base_asset not in assets:
        raise ValueError(f"base_asset '{base_asset}' not found in R.columns")

    other_assets = [a for a in assets if a != base_asset]

    model = ElasticNet(
        alpha=alpha,
        l1_ratio=l1_ratio,
        fit_intercept=False,
        max_iter=10000
    )

    weights_list = []
    dates = []
    yhat_list = []

    n = len(R)

    for t in range(window, n):
        
        R_win = R.iloc[t-window:t]
        Y_win = Y.iloc[t-window:t]


        base_vals = R_win[base_asset].values[:, None]           
        X_diff = R_win[other_assets].values - base_vals         
        y_tilde = (Y_win - R_win[base_asset]).values            
        
        model.fit(X_diff, y_tilde)

        
        w_partial = model.coef_                                 

        
        w_dict = dict(zip(other_assets, w_partial))
        w_dict[base_asset] = 1.0 - w_partial.sum()

        w_full = np.array([w_dict[a] for a in assets])

        date_t = R.index[t]
        weights_list.append(w_full)
        dates.append(date_t)

        
        y_hat_t = float(R.iloc[t].values @ w_full)
        yhat_list.append(y_hat_t)

    weights = pd.DataFrame(weights_list, index=dates, columns=assets)
    yhat_name = (Y.name + "_hat_enet") if (getattr(Y, "name", None) is not None) else "Y_hat_enet"
    Y_hat = pd.Series(yhat_list, index=dates, name=yhat_name)

    return weights, Y_hat

In [ ]:
weights_rmpi, rmpi_hat = dynamic_inflation_hedge_enet(
    R_rmpi, Y_rmpi,
    window=60,
    alpha=1e-3,
    l1_ratio=0.05,
    base_asset="USDCAD"
)
metrics_rmpi = evaluate_hedge(Y_rmpi, rmpi_hat)
metrics_rmpi

{'tracking_error_std': 0.056066500652463366,
 'R2': 0.888944180972064,
 'corr': 0.9478376583771898,
 'mean_bias': -0.0018208587930525352,
 'window': 130}

In [ ]:

weights_ippi, ippi_hat = dynamic_inflation_hedge_enet(
    R_ippi, Y_ippi,
    window=60,
    alpha=1e-3,
    l1_ratio=0.01,
    base_asset="USDCAD"
)

metrics_ippi = evaluate_hedge(Y_ippi, ippi_hat)
metrics_ippi

{'tracking_error_std': 0.01875917433102109,
 'R2': 0.884442748800943,
 'corr': 0.9488082844985571,
 'mean_bias': -0.00468619034030963,
 'window': 130}

In [ ]:



mean_abs = weights_ippi.abs().mean().sort_values(ascending=False)
top5_assets = mean_abs.index[:5]


w_top5_abs = weights_ippi[top5_assets].abs()


fig = go.Figure()

blue_palette = [
    "#08306b",  
    "#08519c",
    "#2171b5",
    "#6baed6",
    "#c6dbef"   
]

for i, col in enumerate(top5_assets):
    fig.add_trace(
        go.Scatter(
            x=w_top5_abs.index,
            y=w_top5_abs[col],
            mode="lines",
            name=col,
            line=dict(color=blue_palette[i], width=1.5),
            stackgroup="one"    
        )
    )

fig.update_layout(
    title="Top 5 IPPI Hedge Assets by |Weight|",
    xaxis_title="Date",
    yaxis_title="Absolute portfolio weight",
    template="plotly_white",
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)

fig.show()


In [ ]:
rmpi_fx_weight = weights_rmpi[cross.columns.tolist()].abs().sum(axis=1)/weights_rmpi.abs().sum(axis=1)
ippi_fx_weight = weights_ippi[cross.columns.tolist()].abs().sum(axis=1)/weights_ippi.abs().sum(axis=1)


In [ ]:
rmpi_fx = rmpi_fx_weight.sort_index().rename("RMPI FX weight")

fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=rmpi_fx.index,
        y=rmpi_fx,
        mode="lines",
        name="RMPI FX weight",
        line=dict(color="rgba(0, 76, 153, 1)", width=2),   # dark blue
        fill="tozeroy"  
    )
)

fig.update_layout(
    title="FX Share in RMPI Hedge Portfolio",
    xaxis_title="Date",
    yaxis_title="Share of portfolio in FX assets",
    template="plotly_white",
    yaxis=dict(range=[0.15, .6])  
)

fig.show()

In [ ]:
import plotly.graph_objects as go

ippi_fx = ippi_fx_weight.sort_index().rename("IPPI FX weight")

fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=ippi_fx.index,
        y=ippi_fx,
        mode="lines",
        name="IPPI FX weight",
        line=dict(color="rgba(0, 76, 153, 1)", width=2),
        fill="tozeroy"  
    )
)


fig.add_vline(
    x="2025-01-01",
    line_width=2,
    line_dash="dash",
    line_color="red"
)


fig.add_annotation(
    x="2025-01-01",
    y=0.74,  
    text="Trump presidency start",
    showarrow=True,
    arrowhead=2,
    ax=40,   
    ay=-40   
)

fig.update_layout(
    title="FX Share in IPPI Hedge Portfolio",
    xaxis_title="Date",
    yaxis_title="Share of portfolio in FX assets",
    template="plotly_white",
    yaxis=dict(range=[0.5, 0.75])
)

fig.show()


In [ ]:
net_exports = exports - imports

In [ ]:
df = pd.concat([ppi['IPPI'],rmpi['RMPI'],net_non_energy_df,net_energy_balance_df],axis=1).dropna()



In [ ]:
x1 = df["RMPI"]
y1 = df["Net energy trade balance"]

x2 = df["IPPI"]
y2 = df["Net non-energy trade balance"]

fig, axes = plt.subplots(1, 2, figsize=(14, 6))


for ax in axes:
    ax.set_facecolor("#f3f6fa")              
    ax.grid(color="white", linewidth=1)      
    for spine in ax.spines.values():         
        spine.set_visible(False)


c1 = (y1 - y1.min()) / (y1.max() - y1.min())
c2 = (y2 - y2.min()) / (y2.max() - y2.min())


ax1 = axes[0]
sc1 = ax1.scatter(
    x1, y1,
    c=plt.cm.twilight(c1),      
    s=25,
    alpha=0.8,
    edgecolor="white",
    linewidth=0.4
)


b1, a1 = np.polyfit(x1, y1, 1)
xline1 = np.linspace(x1.min(), x1.max(), 100)
ax1.plot(xline1, a1 + b1 * xline1, color="#555555", linewidth=2)

ax1.set_title("RMPI vs Net Energy Trade Balance")
ax1.set_xlabel("RMPI (Raw Material Price Index)")
ax1.set_ylabel("Net Energy Trade Balance")


ax2 = axes[1]
sc2 = ax2.scatter(
    x2, y2,
    c=plt.cm.twilight(c2),
    s=25,
    alpha=0.8,
    edgecolor="white",
    linewidth=0.4
)


b2, a2 = np.polyfit(x2, y2, 1)
xline2 = np.linspace(x2.min(), x2.max(), 100)
ax2.plot(xline2, a2 + b2 * xline2, color="#555555", linewidth=2)

ax2.set_title("IPPI vs Net Non-Energy Trade Balance")
ax2.set_xlabel("IPPI (Industrial Product Price Index)")
ax2.set_ylabel("Net Non-Energy Trade Balance")

plt.tight_layout()
plt.show()

In [ ]:

corr = df.corr()
abs_corr = corr.abs()


heat = go.Heatmap(
    z=abs_corr.values,
    x=abs_corr.columns,
    y=abs_corr.index,
    colorscale="Blues",
    zmin=0.5,
    zmax=1,
)

fig = go.Figure(data=heat)


for i, row in enumerate(corr.index):
    for j, col in enumerate(corr.columns):
        fig.add_annotation(
            x=col,
            y=row,
            text=f"{corr.iloc[i, j]:.2f}",
            showarrow=False,
            font=dict(color="black", size=11)
        )


fig.update_layout(
    title="Correlation Matrix",
    xaxis=dict(side="top"),
    yaxis=dict(autorange="reversed"),
    template="plotly_white"
)

fig.show()

In [ ]:
df = df.copy()
df.index = pd.to_datetime(df.index)

fig = go.Figure()


fig.add_trace(
    go.Scatter(
        x=df.index,
        y=df["IPPI"],
        mode="lines",
        name="IPPI",
        line=dict(color="rgba(0, 76, 153, 1)", width=3)  # dark blue
    )
)


fig.add_trace(
    go.Bar(
        x=df.index,
        y=df["Net non-energy trade balance"],
        name="Net non-energy trade balance",
        marker=dict(color="rgba(102, 178, 255, 0.6)"),  # lighter blue
        yaxis="y2"
    )
)

fig.update_layout(
    title="IPPI vs Net non-energy trade balance",
    xaxis=dict(title="Date"),
    yaxis=dict(
        title="RMPI (index)",
        range=[70, 140]
    ),
    yaxis2=dict(
        title="Net non-energy trade balance",
        overlaying="y",
        side="right",
        range=[-1000, -22000]
    ),
    barmode="overlay",
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    template="plotly_white"
)

fig.show()

In [ ]:
det = pd.read_csv('index.csv',index_col = 0).T
det.index = pd.to_datetime(det.index, format='%y-%b', errors='coerce')
det

RMPI     IPPI
2002-01-01  56.4000  76.2000
2002-02-01  57.7000  76.6000
2002-03-01  60.9000  77.1000
2002-04-01  61.6000  77.3000
2002-05-01  62.3000  76.8000
...             ...      ...
2025-06-01 144.4000 130.2000
2025-07-01 144.7000 131.0000
2025-08-01 143.6000 131.4000
2025-09-01 146.1000 132.7000
2025-10-01 148.4000 134.7000

[286 rows x 2 columns]

In [ ]:
margins = pd.read_csv('margines.csv',index_col=0,parse_dates=[0])
margins.index = margins.index.strftime('%Y')


In [ ]:
import plotly.express as px

df = det.reset_index().rename(columns={"index": "Date"})

fig = px.line(
    df,
    x="Date",
    y=["RMPI", "IPPI"],
    title="RMPI and IPPI",
    color_discrete_sequence=["#195f91", "#7cbee5"]  
)
fig.show()